# Harmonic Rule Scoring Notebook
Last Updated August 29 2023

In [1]:
import os
import requests
import json
import ast
import pandas as pd

In [2]:
def load_credentials(credentials_file):
    from ibm_watson_studio_lib import access_project_or_space
    wslib = access_project_or_space()
    
    for file in [credentials_file]:
        data = wslib.load_data(file)
        with open(f"./{file}", "wb") as f:
            f.write(data.read())

### Create the Bearer Token

In [3]:
credentials_file = "../../config/credentials/wml-credentials.json"
with open(credentials_file, "r") as f:
    credentials = json.load(f)

In [4]:
# Assuming you have these variables set somewhere in your script
USERNAME = credentials["username"]
API_KEY = credentials["apikey"]
DATAPLATFORM_URL = credentials["url"]

In [5]:
headers = {
    'Content-type': 'application/json'
}
data = {
    'username': USERNAME,
    'api_key': API_KEY
}

In [6]:
response = requests.post(
    f"{DATAPLATFORM_URL}/icp4d-api/v1/authorize", 
    headers=headers, 
    data=json.dumps(data),
    verify=False  # This corresponds to the '-k' or '--insecure' flag in curl
)
token = response.text
dict_token = ast.literal_eval(token)
bearer_token = dict_token['token']

/Users/jzhou/anaconda3/lib/python3.10/site-packages/urllib3/connectionpool.py:1056: InsecureRequestWarning: Unverified HTTPS request is being made to host 'cpd-ibm-cpd.mas-demo-cp4d-822c5cdfc486f5db3c3145c89ca6409d-0000.us-south.containers.appdomain.cloud'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(


### Load the Data

In [7]:
data_path = '../../data/harmonic_rule/harmonic_training.csv'

In [8]:
df = pd.read_csv(data_path)

In [9]:
df.head(5)

datetime  THDVL1  THDVL2  THDVL3
0  2019-06-25 12:30:00     0.0     0.0     0.0
1  2019-06-25 12:45:00     0.0     0.0     0.0
2  2019-06-25 13:00:00     0.0     0.0     0.0
3  2019-06-25 13:15:00     0.0     0.0     0.0
4  2019-06-25 13:30:00     0.0     0.0     0.0

In [10]:
df.columns

Index(['datetime', 'THDVL1', 'THDVL2', 'THDVL3'], dtype='object')

### Choose all three electrical lines

In [11]:
selected_columns = ['datetime','THDVL1',  'THDVL2', 'THDVL3']

In [12]:
df_score_all = df[selected_columns]

In [13]:
df_score_all = df_score_all.dropna()
df_score_all = df_score_all.reset_index(drop=True)

In [14]:
df_score_all.head(100)

datetime  THDVL1  THDVL2  THDVL3
0   2019-06-25 12:30:00     0.0     0.0     0.0
1   2019-06-25 12:45:00     0.0     0.0     0.0
2   2019-06-25 13:00:00     0.0     0.0     0.0
3   2019-06-25 13:15:00     0.0     0.0     0.0
4   2019-06-25 13:30:00     0.0     0.0     0.0
..                  ...     ...     ...     ...
95  2019-06-26 12:15:00     0.0     0.0     0.0
96  2019-06-26 12:30:00     0.0     0.0     0.0
97  2019-06-26 12:45:00     0.0     0.0     0.0
98  2019-06-26 13:00:00     0.0     0.0     0.0
99  2019-06-26 13:15:00     0.0     0.0     0.0

[100 rows x 4 columns]

In [15]:
df.shape   # 28176

(28177, 4)

In [16]:
df.shape

(28177, 4)

In [17]:
array_of_input_fields = list(df_score_all.columns) 
array_of_values_to_be_scored = df_score_all[array_of_input_fields].values.tolist()

print("Input Data")
print(array_of_input_fields)
df_score_all[array_of_input_fields].head(10)

Input Data
['datetime', 'THDVL1', 'THDVL2', 'THDVL3']


datetime  THDVL1  THDVL2  THDVL3
0  2019-06-25 12:30:00     0.0     0.0     0.0
1  2019-06-25 12:45:00     0.0     0.0     0.0
2  2019-06-25 13:00:00     0.0     0.0     0.0
3  2019-06-25 13:15:00     0.0     0.0     0.0
4  2019-06-25 13:30:00     0.0     0.0     0.0
5  2019-06-25 13:45:00     0.0     0.0     0.0
6  2019-06-25 14:00:00     0.0     0.0     0.0
7  2019-06-25 14:15:00     0.0     0.0     0.0
8  2019-06-25 14:30:00     0.0     0.0     0.0
9  2019-06-25 14:45:00     0.0     0.0     0.0

In [18]:
array_of_input_fields

['datetime', 'THDVL1', 'THDVL2', 'THDVL3']

In [19]:
array_of_values_to_be_scored

[['2019-06-25 12:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 12:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 13:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 13:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 13:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 13:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 14:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 14:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 14:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 14:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 15:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 15:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 15:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 15:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 16:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 16:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 16:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 16:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 17:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 17:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 17:30:00', 0.0, 0.0, 0.0],
 ['2019-06-25 17:45:00', 0.0, 0.0, 0.0],
 ['2019-06-25 18:00:00', 0.0, 0.0, 0.0],
 ['2019-06-25 18:15:00', 0.0, 0.0, 0.0],
 ['2019-06-25 18

In [20]:
import urllib3, requests, json

scoring_url = 'https://cpd-ibm-cpd.mas-demo-cp4d-822c5cdfc486f5db3c3145c89ca6409d-0000.us-south.containers.appdomain.cloud/ml/v4/deployments/14b272a1-111b-4196-9b07-eec757faaaca/predictions?version=2023-08-29'

header = {'Content-Type': 'application/json', 'Authorization': 'Bearer ' + bearer_token}

# NOTE: manually define and pass the array(s) of values to be scored in the next line
payload_scoring = {"input_data": [{"fields": array_of_input_fields, "values": array_of_values_to_be_scored}]}
print("Input payload")
print(json.dumps(payload_scoring, indent=2))

response_scoring = requests.post(scoring_url, json=payload_scoring, headers=header, verify=False)
print("Scoring response")
predictions = json.loads(response_scoring.text)
print(json.dumps(predictions, indent=2))

Input payload
{
  "input_data": [
    {
      "fields": [
        "datetime",
        "THDVL1",
        "THDVL2",
        "THDVL3"
      ],
      "values": [
        [
          "2019-06-25 12:30:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 12:45:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 13:00:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 13:15:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 13:30:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 13:45:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 14:00:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 14:15:00",
          0.0,
          0.0,
          0.0
        ],
        [
          "2019-06-25 14:30:00",
          0.0,


/Users/jzhou/anaconda3/lib/python3.10/site-packages/urllib3/connectionpool.py:1056: InsecureRequestWarning: Unverified HTTPS request is being made to host 'cpd-ibm-cpd.mas-demo-cp4d-822c5cdfc486f5db3c3145c89ca6409d-0000.us-south.containers.appdomain.cloud'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [21]:
output = predictions["predictions"][0]["values"]

In [22]:
output

[[[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 0, 0]],
 [[0, 